In [2]:
!pip install lets_plot -U
!pip install geopandas

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 3.0 MB 19.9 MB/s 
     |████████████████████████████████| 58 kB 2.6 MB/s 
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 1.1 MB 29.0 MB/s 
     |████████████████████████████████| 7.8 MB 79.6 MB/s 
     |████████████████████████████████| 16.6 MB 72.5 MB/s 


In [3]:
import pandas as pd
import geopandas as gpd
import numpy as np
from scipy.interpolate import griddata


from lets_plot import *
from lets_plot.geo_data import *
LetsPlot.setup_html()

import lets_plot
lets_plot.__version__

The geodata is provided by © OpenStreetMap contributors and is made available here under the Open Database License (ODbL).


'2.5.1'

In [4]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [5]:
income_dat = pd.read_csv('drive/MyDrive/kaggle_income.csv', encoding='latin-1')
income_dat.head(3)

id  State_Code State_Name State_ab          County        City  \
0  1011000           1    Alabama       AL   Mobile County   Chickasaw   
1  1011010           1    Alabama       AL  Barbour County  Louisville   
2  1011020           1    Alabama       AL   Shelby County  Columbiana   

             Place  Type Primary  Zip_Code Area_Code     ALand  AWater  \
0   Chickasaw city  City   place     36611       251  10894952  909156   
1        Clio city  City   place     36048       334  26070325   23254   
2  Columbiana city  City   place     35051       205  44835274  261034   

         Lat        Lon   Mean  Median  Stdev        sum_w  
0  30.771450 -88.079697  38773   30506  33101  1638.260513  
1  31.708516 -85.611039  37725   19528  43789   258.017685  
2  33.191452 -86.615618  54606   31930  57348   926.031000

In [6]:
income_dat = income_dat[~income_dat["State_Name"].isin(["Alaska", "Hawaii", "Puerto Rico"])]
income_dat = income_dat[income_dat["Mean"] > 0]
mean_US = income_dat["Mean"].describe()["mean"]
mean_US

67719.94988293362

In [7]:
state_gcoder = geocode_states("US-48")
state_gcoder.get_geocodes().head(3)

id          state     found name                               centroid  \
0  63512          Maine          Maine  [-69.1608471741827, 45.2623642981052]   
1  67213  New Hampshire  New Hampshire  [-71.5517876605831, 44.0015134960413]   
2  60759        Vermont        Vermont   [-72.772353529363, 43.8718488067389]   

                                            position  \
0  [-71.0841688513756, 43.0649779736996, -66.9498...   
1  [-72.5572353601456, 42.6972283422947, -70.7018...   
2  [-73.4377402067184, 42.7269606292248, -71.4653...   

                                               limit  
0  [-71.0841688513756, 42.9808665812016, -66.9498...  
1  [-72.5572353601456, 42.6972283422947, -70.7018...  
2  [-73.4377402067184, 42.7269606292248, -71.4653...

#Reported Mean Income at the location

In [12]:
(ggplot() + 
 geom_map(map=state_gcoder) + 
 geom_point(aes("Lon", "Lat", color="Mean"), data=income_dat, size=1))

#Better Scattering of the Map

In [ ]:
fill_PiYG= scale_fill_gradient2(name="Mean income", 
                                low="#8e0152",mid="#f7f7f7",high="#276419", 
                                midpoint=mean_US)
color_PiYG = scale_color_gradient2(name="Mean income", 
                                   low="#8e0152",mid="#f7f7f7",high="#276419", 
                                   midpoint=mean_US)

# Define some setting to use on plots later on:
# - Remove axis.
# - Define plot coordinate system and size.
map_settings = (theme(axis="blank", panel_grid="blank") +
                coord_fixed(1.27) +
                ggsize(785, 350))

# Customize the tooltip.
tooltip_scatter=(layer_tooltips()
    .format('Mean', '.2s')
    .line("Mean income|$@Mean"))

In [ ]:
(ggplot() + 
 geom_map(map=state_gcoder) +
 geom_point(aes("Lon", "Lat", color="Mean"), 
            data=income_dat, 
            size=1, 
            tooltips=tooltip_scatter) + 
 map_settings + color_PiYG)

In [ ]:
mean_income_state = income_dat.groupby("State_Name", as_index=False)["Mean"].mean()
mean_income_state.head(3)

State_Name          Mean
0    Alabama  54023.752874
1    Arizona  63400.114943
2   Arkansas  52213.932153

#Statewise Mean Income Distribution

In [ ]:
tooltip_state=(layer_tooltips()
          .format('Mean', '.2s')
          .title('@State_Name')
          .line('Mean income|$@Mean'))

# Create a choropleth of the mean income using our `state_gcoder`
(ggplot(mean_income_state) + 
 geom_polygon(aes(fill="Mean"), 
              # Use geocoder with a slightly better resolution for the boundaries.
              map=state_gcoder.inc_res(), 
              # Use "State_Name" value in the data as a key for joining it with the "map".
              map_join="State_Name",       
              tooltips=tooltip_state,
              color="white") + 
 map_settings + fill_PiYG)

In [ ]:
import numpy as np
from scipy.interpolate import griddata

def interpolate_us(lons, lats, values, step, method):
    # method : "linear", "cubic" or "nearest".
    
    # target grid to interpolate to
    grid_lons = np.arange(-125, -66, step)
    grid_lats = np.arange(25, 52, step)
    grid_lons, grid_lats = np.meshgrid(grid_lons, grid_lats)
    
    # interpolate
    grid_values = griddata((lons, lats), values, (grid_lons, grid_lats), method)

    # lon, lat, value DataFrame
    return pd.DataFrame(dict(lon=grid_lons.flatten(), 
                           lat=grid_lats.flatten(), 
                           value=grid_values.flatten()))

In [ ]:
# Interpolate the "Mean" value.
X = income_dat.Lon
Y = income_dat.Lat
Z = income_dat.Mean
mean_income_interpolated = interpolate_us(X, Y, Z, step=.3, method="linear")
mean_income_interpolated.head(3)

lon   lat  value
0 -125.0  25.0    NaN
1 -124.7  25.0    NaN
2 -124.4  25.0    NaN

#Tile Map

In [ ]:
(ggplot(mean_income_interpolated) + 
 geom_tile(aes("lon", "lat", fill="value")) + 
 geom_map(map=state_gcoder, size=.5, color="dark_magenta") +
 map_settings + fill_PiYG)

In [ ]:
# Apply 'spatial union' operation.
states_union = state_gcoder.get_boundaries().geometry.unary_union

# Pick the biggest polygon.
states_union = max(states_union, key=lambda p: p.area)
# boundary_us = gpd.GeoDataFrame({"geometry": [states_union]})
# ggplot() + geom_map(map=boundary_us)

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:5: ShapelyDeprecationWarning: Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.
  """


In [ ]:
from shapely.geometry import Point

mask = mean_income_interpolated.apply(lambda p: states_union.contains(Point(p.lon, p.lat)), axis=1)
mean_income_interpolated_masked = mean_income_interpolated[mask]

In [ ]:
tooltip_tiles=(layer_tooltips()
    .format('value', '.2s')
    .line("Mean income|$@value"))

# Create a tile map with 'masked' data.
(ggplot(mean_income_interpolated_masked) + 
 geom_tile(aes("lon", "lat", fill="value"), tooltips=tooltip_tiles) + 
 geom_map(map=state_gcoder, size=.5, color="dark_magenta") +
 map_settings + fill_PiYG)

#Interactive map of Bay Area, California

In [ ]:
(ggplot(mean_income_interpolated_masked) +
 geom_livemap(zoom=6) +
 geom_tile(aes("lon", "lat", fill="value"), alpha=.7, tooltips=tooltip_tiles) + 
 map_settings + fill_PiYG)